<center><h1> COVID-19 Cases - Plots with Bokeh and Panel </h1><center>

# Developing a Dashboard and With Python Functions



<hr>

> PURPOSE: To build a dashboard with  Panel a PyViz app that would run on a self hosted server

- Categories: [Data Analysis, Data Visualization]
- Author: Thato Seeletso Mmusi

# Table of Contents :
 [Imports](#Imports)
* [Getting the data](#Getting-the-data)
* [Making the map](#Making-the-map)
* [Panel and Bokeh Plots](#Panel-and-Bokeh-Plots)
* [The Interactive Dashboard](#The-Interactive-Dashboard)
* [Running the server locally](#Running-the-server-locally)
* [Deploying Apache](#Deploying-Apache)  
* [References](#References)

# IMPORTS

In [18]:
import pandas as pd
import numpy as np
import matplotlib as mpl
import pylab as plt
pd.set_option('display.width',140)
from bokeh.io import show, output_notebook
from bokeh.models import ColumnDataSource, GeoJSONDataSource, ColorBar, HoverTool, Legend, LogColorMapper, ColorBar
from bokeh.plotting import figure
from bokeh.palettes import brewer
from bokeh.layouts import row, column, gridplot
from bokeh.models import CustomJS, Select, MultiSelect, Plot, LinearAxis, Range1d, DatetimeTickFormatter, DateRangeSlider, GlyphRenderer
from bokeh.models.glyphs import Line, MultiLine
from bokeh.palettes import Category10
output_notebook()
#output_file('test.html')
import panel as pn
import panel.widgets as pnw
pn.extension()
import geopandas as gpd
import json
import datetime

Loading BokehJS ...

# Getting the data

In [2]:
def get_data():
    df = pd.read_excel('https://www.ecdc.europa.eu/sites/default/files/documents/COVID-19-geographic-disbtribution-worldwide.xlsx')
    df['dateRep'] = pd.to_datetime(df.dateRep, infer_datetime_format=True)
    df = df.sort_values(['countriesAndTerritories','dateRep'])
    #days since first case
    #df['days'] = df.dateRep-df.dateRep
    #find cumulative cases in each country by using groupby-apply
    df['totalcases'] = df.groupby(['countriesAndTerritories'])['cases'].apply(lambda x: x.cumsum())
    df['totaldeaths'] = df.groupby(['countriesAndTerritories'])['deaths'].apply(lambda x: x.cumsum())    
    df['deathsper100000'] = df.deaths/df.popData2018
    df['countriesAndTerritories'] = df.countriesAndTerritories.str.replace('_',' ')
    return df

df = get_data()
data = pd.pivot_table(df,index='dateRep',columns='countriesAndTerritories',values='totalcases').reset_index()

In [4]:
summary = df.groupby('countriesAndTerritories')\
            .agg({'deaths':np.sum,'cases':np.sum,'popData2018':np.mean})\
            .reset_index().sort_values('deaths',ascending=False)
summary['ratio'] = summary.deaths/summary.cases

In [5]:
summary

countriesAndTerritories  deaths    cases  popData2018     ratio
200  United States of America   82387  1369964  327167434.0  0.060138
197            United Kingdom   32692   226463   66488991.0  0.144359
99                      Italy   30911   221216   60431283.0  0.139732
70                     France   26991   140227   66987244.0  0.192481
178                     Spain   26920   228030   46723749.0  0.118055
..                        ...     ...      ...          ...       ...
67              Faroe Islands       0      187      48497.0  0.000000
160     Saint Kitts and Nevis       0       15      52441.0  0.000000
68                       Fiji       0       18     883483.0  0.000000
188               Timor Leste       0       24    1267972.0  0.000000
22                     Bhutan       0       11     754394.0  0.000000

[209 rows x 5 columns]

# Making the map

### Panel and Bokeh Plots

In [6]:
def get_geodata(shapefile):

    #Read shapefile using Geopandas
    gdf = gpd.read_file(shapefile)[['ADMIN', 'ADM0_A3', 'geometry']]
    #Rename columns.
    gdf.columns = ['country', 'country_code', 'geometry']
    gdf = gdf.drop(gdf.index[159])
    return gdf

def get_geodatasource(gdf):    
    """Get getjsondatasource from geopandas object"""
    json_data = json.dumps(json.loads(gdf.to_json()))
    return GeoJSONDataSource(geojson = json_data)

def bokeh_plot_map(gdf, column=None, title='', plot_width=650):
    """Plot bokeh map from GeoJSONDataSource """
    
    geosource = get_geodatasource(gdf)
    palette = brewer['OrRd'][8]
    palette = palette[::-1]
    vals = gdf[column]
    columns = ['cases','deaths','ratio','popData2018','countriesAndTerritories']
    x = [(i, "@%s" %i) for i in columns]    
    hover = HoverTool(
        tooltips=x, point_policy='follow_mouse')
    color_mapper = LogColorMapper(palette = palette, low = vals.min(), high = vals.max())
    tools = ['wheel_zoom,pan,reset',hover]
    p = figure(title = title, plot_height=400 , plot_width=plot_width, toolbar_location='right', tools=tools)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    #Add patch renderer to figure
    p.patches('xs','ys', source=geosource, fill_alpha=1, line_width=0.5, line_color='black',  
              fill_color={'field' :column , 'transform': color_mapper})
    p.background_fill_color = "#e1e1ea"
    p.toolbar.logo = None
    p.sizing_mode = 'stretch_width'
    return p

gdf = get_geodata('data/ne_110m_admin_0_countries.shp')
gdf = gdf.merge(summary, left_on='country', right_on='countriesAndTerritories', how='inner')
mp = bokeh_plot_map(gdf, 'cases')
pn.pane.Bokeh(mp)

Bokeh(Figure)

In [7]:
def bokeh_plot_cases(event):
    """Plot cases per country"""
    
    countries = country_select.value[:10]
    scale = scale_select.value
    value = plot_select.value
    rolling = rolling_box.value
    dates = date_slider.value    
    xdf = df[(df.dateRep>dates[0]) & (df.dateRep<dates[1])]
    
    index = 'dateRep'
    axtype = 'datetime'
    colors = Category10[10] + Category10[10]
    items=[]
    if value == 'total vs cases':
        index = 'totalcases'
        value = 'new cases'
        x = df[df.countriesAndTerritories.isin(countries)]
        p = figure(plot_width=600,plot_height=500,
               y_axis_type='log',x_axis_type='log',
               tools=[])
        i=0
        for c,g in x.groupby('countriesAndTerritories'):
            source = ColumnDataSource(g)
            line = Line(x='totalcases',y='cases', line_color=colors[i],line_width=3,line_alpha=.8,name='x')     
            glyph = p.add_glyph(source, line)
            i+=1     
            items.append((c,[glyph]))
    else:
        data = pd.pivot_table(xdf,index=index,columns='countriesAndTerritories',values=value)
        if rolling == True:
            data = data.rolling(4).mean().reset_index()
        else:
            data = data.reset_index()
        source = ColumnDataSource(data)        
        i=0   
        p = figure(plot_width=600,plot_height=500,x_axis_type=axtype,
                   y_axis_type=scale,
                   tools=[])        
        for c in countries:
            line = Line(x=index,y=c, line_color=colors[i],line_width=3,line_alpha=.8,name=c)
            glyph = p.add_glyph(source, line)
            i+=1
            items.append((c,[glyph]))
            
    p.xaxis.axis_label = index
    p.yaxis.axis_label = value        
    p.add_layout(Legend(
                location="top_left",
                items=items))    
    p.background_fill_color = "#e1e1ea"
    p.background_fill_alpha = 0.5
    p.legend.location = "top_left"
    p.legend.label_text_font_size = "9pt"
    p.toolbar.logo = None
    p.sizing_mode = 'scale_height'
    plot_pane.object = p    
    return 

def summary_plot(event=None):
 
    value = 'deaths' #plot_select.value
    x = summary[:10]
    hover = HoverTool(tooltips=[
                ('Cases', '@cases'),
                ('Deaths', '@deaths'),
                ('Population','@popData2018')]
            )
    p = figure(plot_width=300,plot_height=400, y_range=list(x.countriesAndTerritories),               
               x_axis_type='linear', title='Top %s' %value, tools=[hover])
    
    source = ColumnDataSource(summary)
    p.hbar(y='countriesAndTerritories', right=value, left=0.01, height=0.9, color='brown', source=source)  
    p.xaxis.major_label_orientation = 45
    p.background_fill_color = "#e1e1ea"
    p.toolbar.logo = None
    p.sizing_mode = 'scale_height'
    summary_pane.object = p
    return 

# The Interactive Dashboard

In [9]:
#print (summary[:3])
common=['Botswana','South Africa','Zimbabwe','Zambia','Namibia','Lesotho','Eswatini']
totalc = str(df.cases.sum())+' cases'
totald = str(df.deaths.sum())+' deaths'
style = {'font-size': '15pt','color':'blue','margin': '4px'}
#cases_pane = pn.pane.Str(totalc,style=style)
deaths_pane = pn.pane.Str(totald,style=style)
names = list(df.countriesAndTerritories.unique() )
country_select = pnw.MultiSelect(name="Country", value=common[:5], height=140, options=names, width=180)
country_select.param.watch(bokeh_plot_cases, 'value')
scale_select = pnw.Select(name="Scale", value='log', options=['linear','log'], width=180)
scale_select.param.watch(bokeh_plot_cases, 'value')
plot_select = pnw.Select(name="Plot type", value='cases', 
                         options=['cases','totalcases','deaths','totaldeaths','deathsper100000','total vs cases'], width=180)
plot_select.param.watch(bokeh_plot_cases, 'value')
rolling_box = pnw.Checkbox(name='Rolling Average')
rolling_box.param.watch(bokeh_plot_cases, 'value')

start = df.dateRep.min()
end=pd.Timestamp(datetime.date.today())
date_slider = pnw.DateRangeSlider(name="Date", start=start, end=end,
                                  value=(start, end), step=1, width=180)
date_slider.param.watch(bokeh_plot_cases, 'value')
plot_pane = pn.pane.Bokeh()
plot = bokeh_plot_cases(None)
summary_pane = pn.pane.Bokeh()
summary_plot()
plot_select.param.watch(summary_plot, 'value')
mp = bokeh_plot_map(gdf, 'cases')
map_pane = pn.pane.Bokeh(mp,sizing_mode='stretch_width')

title = pn.pane.HTML('<h3>COVID-19 based on ECDC data</h3>',style={'background-color': '#F6F6F6','padding': '5px'})
helptxt = pn.pane.HTML('<p><small>ctrl-click for multiple selections</small></p>')
info = pn.pane.HTML('<a href="https://github.com/Mmusi/COVID-19-Botswana/blob/master/visualizing-with-bokeh">link to original article</a>')
app = pn.Column(title,pn.Row(pn.Column(country_select,scale_select,plot_select,rolling_box,date_slider,helptxt),plot_pane,
                       pn.Column(deaths_pane,summary_pane),
                       sizing_mode='stretch_height'), map_pane, info)
app


Column
    [0] HTML(str, style={'background-color': '#F6F...})
    [1] Row(sizing_mode='stretch_height')
        [0] Column
            [0] MultiSelect(height=140, name='Country', options=['Afghanistan', ...], sizing_mode='fixed', value=['Botswana', 'South Africa...], width=180)
            [1] Select(name='Scale', options=['linear', 'log'], value='log', width=180)
            [2] Select(name='Plot type', options=['cases', 'totalcases', ...], value='cases', width=180)
            [3] Checkbox(name='Rolling Average')
            [4] DateRangeSlider(end=Timestamp('2020-05-14 0..., name='Date', start=Timestamp('2019-12-31 0..., value=(Timestamp('2019-12-31 00:..., width=180)
            [5] HTML(str)
        [1] Bokeh(Figure)
        [2] Column
            [0] Str(str, style={'font-size': '15pt', ...})
            [1] Bokeh(Figure)
    [2] Bokeh(Figure, sizing_mode='stretch_width')
    [3] HTML(str)

In [10]:
summary_plot()

## Using javascript for callbacks

In [11]:
source = ColumnDataSource(data)

#print (filt_data)
# create CDS for filtered sources
filt_data1 = data[['dateRep','Botswana']].rename(columns={'Botswana':'cases'})
src2 = ColumnDataSource(filt_data1)
filt_data2 = data[['dateRep','South Africa']].rename(columns={'South Africa':'cases'})
src3 = ColumnDataSource(filt_data2)

source.add(data['dateRep'].apply(lambda d: d.strftime('%Y-%m-%d')), 'date_formatted')

hover_tool = HoverTool(tooltips=[
            ('Cases', '@cases')]   
        )

p1 = figure(plot_width=850,plot_height=400,x_axis_type='datetime',
           tools=[hover_tool],title='Covid-19 Cases Southern Africa',y_range=Range1d(start=0, end=filt_data1.cases.max()+50))
p1.line(x='dateRep',y='cases', source=src2, legend_label="Country 1", line_color='blue',
        line_width=3,line_alpha=.8)
#set the second y-axis and use that with our second line
p1.extra_y_ranges = {"y2": Range1d(start=0, end=filt_data2.cases.max()+50)}
p1.add_layout(LinearAxis(y_range_name="y2"), 'right')
p1.line(x='dateRep',y='cases', source=src3, legend_label="Country 2", line_color='orange',
        line_width=3,line_alpha=.8,y_range_name="y2")

p1.yaxis[0].axis_label = 'Botswana'
p1.yaxis[1].axis_label = 'South Africa'
p1.background_fill_color = "whitesmoke"
p1.background_fill_alpha = 0.5
p1.legend.location = "top_left"
p1.xaxis.axis_label = 'Date'
p1.xaxis.formatter=DatetimeTickFormatter(days="%d/%m",
months="%m/%d %H:%M",
)
#this javascript snippet is the callback when either select is changed
code="""
var c = cb_obj.value;
ax.axis_label = c;
var y = s1.data[c];
s2.data['cases'] = y;
y_range.start = 0;
y_range.end = parseInt(y[y.length - 1]+50);
s2.change.emit();
"""
callback1 = CustomJS(args=dict(s1=source,s2=src2,y_range=p1.y_range,ax=p1.yaxis[0]), code=code)
callback2 = CustomJS(args=dict(s1=source,s2=src3,y_range=p1.extra_y_ranges['y2'],ax=p1.yaxis[1]), code=code)
names = list(df.countriesAndTerritories.unique() )

select1 = Select(title="Select Other Country:", value='Botswana', options=common)
select1.js_on_change('value', callback1)
select2 = Select(title="Select Other Country:", value='South Africa', options=names)
select2.js_on_change('value', callback2)

layout = column(row(select1,select2), row(p1))
show(layout)

l = column(gridplot([[row(select1, select2)]]), row(p1))
show(l)

## Saving work to html

In [12]:
from bokeh.resources import CDN
from bokeh.embed import file_html

#plot = figure(plot_width=200)
#plot.circle([1,2], [3,4])

html = file_html(l, CDN, "COVID-19 Cases Botswana vs Southern Africa")
outfile = open("covid_case.html",'w')
outfile.write(html)
outfile.close()

In [19]:
from bokeh.resources import CDN
from bokeh.embed import file_html

#plot = figure(plot_width=200)
#plot.circle([1,2], [3,4])

html = file_html(mp, CDN, "COVID-19 Cases Southern Africa")
outfile = open("covid_map.html",'w')
outfile.write(html)
outfile.close()

# Running the server locally

In [13]:
app.servable(title='ECDC COVID-19 dashboard')

Column
    [0] HTML(str, style={'background-color': '#F6F...})
    [1] Row(sizing_mode='stretch_height')
        [0] Column
            [0] MultiSelect(height=140, name='Country', options=['Afghanistan', ...], sizing_mode='fixed', value=['Botswana', 'South Africa...], width=180)
            [1] Select(name='Scale', options=['linear', 'log'], value='log', width=180)
            [2] Select(name='Plot type', options=['cases', 'totalcases', ...], value='cases', width=180)
            [3] Checkbox(name='Rolling Average')
            [4] DateRangeSlider(end=Timestamp('2020-05-14 0..., name='Date', start=Timestamp('2019-12-31 0..., value=(Timestamp('2019-12-31 00:..., width=180)
            [5] HTML(str)
        [1] Bokeh(Figure)
        [2] Column
            [0] Str(str, style={'font-size': '15pt', ...})
            [1] Bokeh(Figure)
    [2] Bokeh(Figure, sizing_mode='stretch_width')
    [3] HTML(str)

In [14]:
from bokeh.io import show, output_file
from bokeh.plotting import figure

output_file("bars.html")

locations = ['Ramotswa', 'Molepolole', 'Gaborone', 'Siviya', 'Metsimotlhabe', 'Mahalapye']

p = figure(x_range=locations, plot_height=250, title="Location Incidents")
p.vbar(x=locations, top=[1, 3, 14, 1, 4, 1], width=0.9)

p.xgrid.grid_line_color = None
p.y_range.start = 0

show(p)

# Deploying Apache

If we wish to share this application beyond a local network. We would have to run the server locally as above and then proxy connections to it through a public web server like Apache. 

To do this would require another tutorial... should you be interested in taking this tutorial a step further please con tact me at the following contacts:

 - https://www.linkedin.com/in/thato-mmusi-13940b5b
 - thatommusi@bonala.biz or mmusi2010@gmail.com
 
 Alternatively to see an example of a simple dashboard resulting from the above work you can click on the link below:
 
 http://www.bonala.biz//?p=blogController&a=covid_19 

# References 

Links 

* https://www.ecdc.europa.eu/en/publications-data/download-todays-data-geographic-distribution-covid-19-cases-worldwide
* https://github.com/dmnfarrell/teaching/blob/master/sarscov2/plot_cases.ipynb
* https://www.kaggle.com/pavlofesenko/interactive-titanic-dashboard-using-bokeh
* https://stackoverflow.com/questions/41382310/adding-a-second-y-axis-in-bokehjs
* https://panel.pyviz.org/index.html
* https://docs.bokeh.org/en/latest/docs/user_guide/server.html#apache

